<a href="https://colab.research.google.com/github/ArjunJSP/quantities/blob/main/testquantities.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **QUANTITIES CALCULATOR: Roper St. Francis Hospital**

# Import .e2k File and Setup Calculator

Mount to Drive Location and double check files in the directory


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

# Navigate to a specific folder in your Google Drive
%cd /content/drive/My Drive/mountlocation

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
/content/drive/My Drive/mountlocation


Import necessary libraries

In [ ]:
import numpy as np
import pandas as pd
from io import StringIO
import re #currently not using
import shlex
import math
import matplotlib.pyplot as plt
import warnings
from openpyxl import load_workbook
from google.colab import data_table
from vega_datasets import data
# pip install XlsxWriter
# import xlsxwriter
from IPython.core.display import display, HTML

data_table.enable_dataframe_formatter()

Define file path:

In [ ]:
filepath = 'RSFH_TOWER_R1_V4.4.4_deletedfloors.e2k'
#Export units for e2k file:
fileunit_length = 'in'
fileunit_weight = 'kip'

# Redefine ETABS .e2k as Dataframes



Computed dataframes include:
>**df_stories**: individual story heights and cumulative elevation in default .e2k units<br>**df_pointcoordinates**: x,y coordinates for each *point label* (note: these labels might be repeated on several stories that share geometry)<br>**df_lineconnectivity**: defines the element type, start and end point label (note: elements that repeat across levels will share a label) <br>**df_areaconnectivity**: defines the element type, point label corners <br>**df_groupassigns**: defines group for each element label (note: groups are associated with element labels, not unique elements) <br>**df_lineassigns**: defines each line based on its label *and* the story it exists on (note: this is currently the most comprehensive df that includes a list entry for every line element in the model) <br>**df_areaassigns**: defines each area based on its label *and* the story it exists on (note: this is currently the most comprehensive df that includes a list entry for every area element in the model)


## Open text file and identify $ headers

In [ ]:
with open(filepath, 'r') as file:
    # Initialize lists to store data
    dollar_lines = []
    line_indices = []
    line_lengths = []

    # Initialize variables
    after_dollar = False
    line_count = 0

    # Read each line in the file
    for idx, line in enumerate(file):
        # Skip the line "$ END OF MODEL FILE"
        if line.strip() == "$ END OF MODEL FILE":
            continue

        # Check if the line starts with '$'
        if line.startswith('$'):
            # Set the flag to True indicating that we are currently reading lines after the '$' line
            after_dollar = True
            # Append the line to the list of dollar lines
            dollar_lines.append(line.strip())
            # Append the index of the line
            line_indices.append(idx)
            # Reset line count
            line_count = 0
        # Check if we are currently reading lines after the '$' line and we encounter a blank line
        elif after_dollar and line.strip() == '':
            # If so, append the line count to the list of line lengths
            line_lengths.append(line_count)
            # Reset the flag indicating that we are no longer reading lines after the '$' line
            after_dollar = False
        # Increment the line count if we are currently reading lines after the '$' line
        elif after_dollar:
            line_count += 1

# Create a DataFrame from the collected data
Data_Indexes = pd.DataFrame({'Line': dollar_lines, 'Index': line_indices, 'Length': line_lengths})

# Print the DataFrame
Data_Indexes


Line  Index  Length
0   $ File G:\My Drive\mountlocation\RSFH_TOWER_R1...      0       0
1                               $ PROGRAM INFORMATION      2       1
2                                          $ CONTROLS      5       5
3                    $ STORIES - IN SEQUENCE FROM TOP     12      11
4                                             $ GRIDS     25      39
5                                   $ DIAPHRAGM NAMES     66       3
6                               $ MATERIAL PROPERTIES     71     149
7                                 $ REBAR DEFINITIONS    222      12
8                                    $ FRAME SECTIONS    236     437
9                         $ AUTO SELECT SECTION LISTS    675      30
10                                $ CONCRETE SECTIONS    707      11
11                                  $ TENDON SECTIONS    720       1
12                                  $ SLAB PROPERTIES    723       2
13                                  $ DECK PROPERTIES    727       5
14                                  $ WALL PROPERTIES    734       6
15                                  $ LINK PROPERTIES    742       3
16                            $ PANEL ZONE PROPERTIES    747       2
17                              $ PIER/SPANDREL NAMES    751       2
18                                $ POINT COORDINATES    755     219
19                              $ LINE CONNECTIVITIES    976     359
20                              $ AREA CONNECTIVITIES   1337      43
21                                           $ GROUPS   1382    3923
22                                    $ POINT ASSIGNS   5307      60
23                                     $ LINE ASSIGNS   5369    6742
24                                     $ AREA ASSIGNS  12113     393
25                                    $ LOAD PATTERNS  12508     116
26                               $ POINT OBJECT LOADS  12626       0
27                               $ FRAME OBJECT LOADS  12628     632
28                          $ SHELL UNIFORM LOAD SETS  13262       8
29                               $ SHELL OBJECT LOADS  13272     786
30                                 $ ANALYSIS OPTIONS  14060      13
31                                      $ MASS SOURCE  14075      20
32                                        $ FUNCTIONS  14097      16
33                        $ GENERALIZED DISPLACEMENTS  14115       0
34                                       $ LOAD CASES  14117     172
35                                $ LOAD COMBINATIONS  14291    1573
36                         $ STEEL DESIGN PREFERENCES  15866      11
37                          $ STEEL DESIGN OVERWRITES  15879    2012
38                      $ CONCRETE DESIGN PREFERENCES  17893       7
39                     $ COMPOSITE DESIGN PREFERENCES  17902      15
40              $ COMPOSITE COLUMN DESIGN PREFERENCES  17919       7
41                          $ WALL DESIGN PREFERENCES  17928       6
42                 $ CONCRETE SLAB DESIGN PREFERENCES  17936       4
43                                       $ TABLE SETS  17942       0
44                        $ DATABASE TABLE NAMED SETS  17944     154
45                              $ PROJECT INFORMATION  18100       1
46                                              $ LOG  18103     993

###Table-Pulling Function

---



In [ ]:
def get_table(table_name, file_name):
  start_index = 1 + Data_Indexes.loc[Data_Indexes['Line'] == table_name, 'Index'].iloc[0]
  end_index = start_index + Data_Indexes.loc[Data_Indexes['Line'] == table_name, 'Length'].iloc[0] -1

  with open(file_name, 'r') as file:
      # Initialize a list to store the extracted lines
      extracted_lines = []

      # Read each line in the file
      for idx, line in enumerate(file):
          # Check if the current index is within the range of the specified indices
          if start_index <= idx <= end_index:
              # Add the line to the list of extracted lines
              extracted_lines.append(line.strip())

  data_array = extracted_lines
  data_list = []

  #__________
  # #define a function that splits along spaces AND between entries bounded by "", so that Group Names can have spaces within them, but not cause splitting issues

  def split_quoted_string(s):
      # Use shlex to split the string respecting quoted substrings
      parts = shlex.split(s)

      # Filter out empty strings
      parts = [part for part in parts if part]

      return parts
  #__________


  # Iterate over each string in the array
  for line in extracted_lines:
      # Split the string based on space delimiters
      # split_line = line.split()
      split_line = split_quoted_string(line)
      # Append the split line to the list of data
      data_list.append(split_line)

  # Create a DataFrame from the list of data
  df = pd.DataFrame(data_list)
  return df

##Story Heights
> df_stories

In [ ]:
df = get_table('$ STORIES - IN SEQUENCE FROM TOP',filepath)

df = df[[1, 3]]
df.columns = ['Level','Height']
#height is reported in inches

# Remove quotation marks from data
for column in df.columns:
  df[column] = df[column].str.replace('"', '')

# Convert 'Height' column values from string to integer
df['Height'] = df['Height'].astype(int)

# Reverse the order of the column 'values'
reversed_values = df['Height'][::-1]

# Calculate the reverse cumulative sum
df['Elevation'] = reversed_values.cumsum()[::-1]

df_stories = df
df_stories

Level  Height  Elevation
0    L10     240       1890
1    L09     174       1650
2    L08     174       1476
3    L07     174       1302
4    L06     174       1128
5    L05     174        954
6    L04     174        780
7    L03     174        606
8    L02     228        432
9    L01     204        204
10   L00       0          0

## Find Point Coordinates
> df_pointcoordinates



In [ ]:
df3 = get_table('$ POINT COORDINATES',filepath)

df3 = df3[[1, 2, 3]]
df3.columns = ['PointID','x','y']

# Remove quotation marks from data
for column in df3.columns:
  df3[column] = df3[column].str.replace('"', '')
df_pointcoordinates = df3
df_pointcoordinates

PointID          x          y
0         1  -2878.141  -5149.223
1         2  -2878.141   142.7768
2         3  -2500.141  -5149.223
3         4  -2500.141  -4393.223
4         5  -2500.141  -3637.223
..      ...        ...        ...
214     215  -1666.141  -1558.223
215     216  -1666.141  -1180.223
216     217  -1666.141  -802.2232
217     218  -1666.141  -424.2232
218     219  -1666.141  -46.22318

[219 rows x 3 columns]

## Find Line Connectivities
>df_lineconnectivity

In [ ]:
df2 = get_table('$ LINE CONNECTIVITIES', filepath)

df2 = df2[[1, 2, 3, 4, 5]]
df2.columns = ['ElemID','ElemType','iPointID','jPointID', 'MultiLevel']
# Multi Level Refers to a true/false if the element spans multiple floors, ie. a Column or Brace extends from its Level assignment down to the elevation of the level below.

# Remove quotation marks from data
for column in df2.columns:
  df2[column] = df2[column].str.replace('"', '')

df2['MultiLevel'] = df2['MultiLevel'].astype(int)

df_lineconnectivity = df2

df_lineconnectivity.to_csv('df_lineconnectivity.txt', sep='\t', index=False)

df_lineconnectivity

ElemID ElemType iPointID jPointID  MultiLevel
0       C1   COLUMN        1        1           1
1       C2   COLUMN        2        2           1
2       C3   COLUMN        3        3           1
3       C4   COLUMN        4        4           1
4       C5   COLUMN        5        5           1
..     ...      ...      ...      ...         ...
354   L355     LINE       27        9           0
355   L356     LINE        9       28           0
356   L357     LINE       28       16           0
357   L358     LINE       16       29           0
358   L359     LINE       29       18           0

[359 rows x 5 columns]

## Find Area Connectivities
>df_areaconnectivity

In [ ]:
df2 = get_table('$ AREA CONNECTIVITIES',filepath)

df2 = df2[[1, 2, 4, 5, 6, 7]]
df2.columns = ['ElemID','ElemType','iPointID','jPointID','kPointID','lPointID']

# Remove quotation marks from data
for column in df2.columns:
  df2[column] = df2[column].str.replace('"', '')
df_areaconnectivity = df2
df_areaconnectivity

ElemID ElemType iPointID jPointID kPointID lPointID
0      F1    FLOOR       73       59        9        2
1      F2    FLOOR       16       63       83       18
2      F3    FLOOR       16        9       59       63
3      F4    FLOOR        3       56       64        1
4      F5    FLOOR       74       17       10       60
5      F6    FLOOR       65       64       56        4
6      F7    FLOOR       60       11        4       56
7      F8    FLOOR       74       75       11       60
8      F9    FLOOR       65        4       57       66
9     F10    FLOOR       11        4       57       61
10    F11    FLOOR       75       76       61       11
11    F12    FLOOR       67       66       57        5
12    F13    FLOOR        5       57       61       12
13    F14    FLOOR       76       61       12       77
14    F15    FLOOR       68       67        5       33
15    F16    FLOOR       37       33        5       12
16    F17    FLOOR       78       37       12       77
17    F18    FLOOR       30       68       33       34
18    F19    FLOOR       38       34       33       37
19    F20    FLOOR       78       41       38       37
20    F21    FLOOR       31       30       34        6
21    F22    FLOOR        6       34       38       13
22    F23    FLOOR       41       42       13       38
23    F24    FLOOR       32       31        6       35
24    F25    FLOOR       13       39       35        6
25    F26    FLOOR       43       39       13       42
26    F27    FLOOR       69       32       35       36
27    F28    FLOOR       35       36       40       39
28    F29    FLOOR       43       79       40       39
29    F30    FLOOR       69       36        7       70
30    F31    FLOOR        7       14       40       36
31    F32    FLOOR       80       14       40       79
32    F33    FLOOR       71       70        7       58
33    F34    FLOOR       14       62       58        7
34    F35    FLOOR       80       81       62       14
35    F36    FLOOR       71       58        8       72
36    F37    FLOOR        8       58       62       15
37    F38    FLOOR       81       62       15       82
38    F39    FLOOR       73       72        8       59
39    F40    FLOOR       59        8       15       63
40    F41    FLOOR       82       83       63       15
41    F42    FLOOR        3       56       60       10
42    F43    FLOOR       42       43       39       13

## Find Group Assignments
>df_groupassigns


In [ ]:
df = get_table('$ GROUPS',filepath)
df = df[[1, 3, 4]]
# df.rename(columns={1: 'FrameID', 2: 'Level', 4: 'Section'})
# Remove quotation marks from data
for column in df.columns:
    df[column] = df[column].str.replace('"', '')

#reanme dataframe columns
df.columns = ['Group','ElemID','Level']

df_groupassigns = df
df_groupassigns.to_csv('df_groupassigns.txt', sep='\t', index=False)

df_groupassigns

Group ElemID Level
0     BRB-X-Col.-T1   None  None
1     BRB-X-Col.-T1     C1   L01
2     BRB-X-Col.-T1     C1   L02
3     BRB-X-Col.-T1     C2   L01
4     BRB-X-Col.-T1     C2   L02
...             ...    ...   ...
3918         MS-L06   None  None
3919         MS-L07   None  None
3920         MS-L08   None  None
3921         MS-L09   None  None
3922         MS-L10   None  None

[3923 rows x 3 columns]

## Find Line Assigns
>df_lineassigns

In [ ]:
df = get_table('$ LINE ASSIGNS',filepath)
# Create a DataFrame from the list of data
# df = pd.DataFrame(data_list)
df = df[[1, 2, 4]]
df.rename(columns={1: 'FrameID', 2: 'Level', 4: 'Section'})
# Remove quotation marks from data
for column in df.columns:
    df[column] = df[column].str.replace('"', '')

# Calculate the midpoint index
midpoint_index = len(df) // 2

# Crop the DataFrame in half
df_lineassigns = df.iloc[:midpoint_index]
df_lineassigns.columns = ['ElemID','Level','Section']

df_lineassigns.to_csv('lineassigns.txt', sep='\t', index=False)

df_lineassigns

ElemID Level               Section
0        C1   L01  BU-WF-26X26X6X6-GR50
1        C1   L02  BU-WF-26X26X6X6-GR50
2        C2   L01  BU-WF-26X26X6X6-GR50
3        C2   L02  BU-WF-26X26X6X6-GR50
4        C3   L01  BU-WF-26X26X6X6-GR50
...     ...   ...                   ...
3366   L335   L10                  NONE
3367   L336   L10                  NONE
3368   L337   L10                  NONE
3369   L338   L10                  NONE
3370   L339   L10                  NONE

[3371 rows x 3 columns]

## Find Area Assigns
>df_areaassigns

In [ ]:
df = get_table('$ AREA ASSIGNS',filepath)
# Create a DataFrame from the list of data
# df = pd.DataFrame(data_list)
df = df[[1, 2, 4]]
df.rename(columns={1: 'AreaID', 2: 'Level', 4: 'Section'})
# Remove quotation marks from data
for column in df.columns:
    df[column] = df[column].str.replace('"', '')

# # Calculate the midpoint index
# midpoint_index = len(df) // 2

# Crop the DataFrame in half
df_areaassigns = df.iloc[:midpoint_index]
df_areaassigns.columns = ['ElemID','Level','Section']
df_areaassigns

ElemID Level           Section
0       F1   L01  SD3+4.5-4KSI-NWC
1       F2   L01  SD3+4.5-4KSI-NWC
2       F3   L01  SD3+4.5-4KSI-NWC
3       F4   L01  SD3+4.5-4KSI-NWC
4       F5   L01  SD3+4.5-4KSI-NWC
..     ...   ...               ...
388    F28   L10    SD3+8-4KSI-NWC
389    F29   L10    SD3+8-4KSI-NWC
390    F30   L10    SD3+8-4KSI-NWC
391    F31   L10    SD3+8-4KSI-NWC
392    F32   L10    SD3+8-4KSI-NWC

[393 rows x 3 columns]

#Assemble Frame Quantity Table


- associating the element assignment with its section, group, connectivity, and AISC unit weight.
- setting non-standard AISC section weights to zero (will need manual assignmnents)
>df_lines

## Referencing the AISC Excel Table
>df_AISC

In [ ]:
steel_dbs= {'AISC v15.0':
 {'file_path':
  "/content/drive/Shareddrives/Firm-wide Structural Resources/02.General Project Resources/02.06.Spreadsheets/02.06.09 Analysis-Steel/AISC v15 Shapes Database.xlsx",
  'sheet_name': "Database v15.0",
  'US': 'A:CF',
  'Metric': ['A, CG:FJ']}}

STEEL_DB = 'AISC v15.0'
UNITS = 'US'

df_AISC = pd.read_excel(steel_dbs[STEEL_DB]['file_path'],
                         sheet_name=steel_dbs[STEEL_DB]['sheet_name'],
                         usecols=steel_dbs[STEEL_DB][UNITS],
                         header=0)

df_AISC
# #using the .at function to lookup values in the section database and then .loc to find information about that section, ie. the weight ('W') based on steeel)_db database column labels
# member_section.at[1,'Section']
# #note: this will break for NONE sections!
# steel_db.loc[steel_db['AISC_Manual_Label']== (member_section.at[1,'Section']),'W'].values[0]

Type EDI_Std_Nomenclature AISC_Manual_Label T_F       W       A     d  \
0        W              W44X335           W44X335   F  335.00   98.50    44   
1        W              W44X290           W44X290   F  290.00   85.40  43.6   
2        W              W44X262           W44X262   F  262.00   77.20  43.3   
3        W              W44X230           W44X230   F  230.00   67.80  42.9   
4        W              W40X655           W40X655   T  655.00  193.00  43.6   
...    ...                  ...               ...  ..     ...     ...   ...   
2086  PIPE             Pipe5XXS          Pipe5XXS   F   38.60   10.70     –   
2087  PIPE             Pipe4XXS          Pipe4XXS   F   27.60    7.66     –   
2088  PIPE             Pipe3XXS          Pipe3XXS   F   18.60    5.17     –   
2089  PIPE         Pipe2-1/2XXS      Pipe2-1/2XXS   F   13.70    3.83     –   
2090  PIPE             Pipe2XXS          Pipe2XXS   F    9.04    2.51     –   

        ddet Ht  h  ...   rts    ho   PA PA2   PB   PC   PD   T  WGi WGo  
0         44  –  –  ...  4.24  42.2  132   –  148  104  120  38  5.5   –  
1     43.625  –  –  ...   4.2    42  131   –  147  103  119  38  5.5   –  
2      43.25  –  –  ...  4.17  41.9  131   –  147  102  118  38  5.5   –  
3     42.875  –  –  ...  4.13  41.7  130   –  146  102  118  38  5.5   –  
4     43.625  –  –  ...  4.71  40.1  132   –  149  104  121  34  7.5   –  
...      ... .. ..  ...   ...   ...  ...  ..  ...  ...  ...  ..  ...  ..  
2086       –  –  –  ...     –     –    –   –    –    –    –   –    –   –  
2087       –  –  –  ...     –     –    –   –    –    –    –   –    –   –  
2088       –  –  –  ...     –     –    –   –    –    –    –   –    –   –  
2089       –  –  –  ...     –     –    –   –    –    –    –   –    –   –  
2090       –  –  –  ...     –     –    –   –    –    –    –   –    –   –  

[2091 rows x 84 columns]

## Assembly of df_lines

In [ ]:
#merge the line assignments (comprised of a value entry for each line label in the model) with the line connectivity (describing how that line connects to joint labels)
#note: the labels are not unique IDs; each line label can represent multiple lines that are identical across multiple floors

df_lines = pd.merge(df_lineassigns,df_lineconnectivity, on='ElemID')

#merge the line data with group assignments
#note: since line labels can be repeated across floors, the merge must use two keys: the line label (ElemID) and the level it is on (Level)

df_lines = pd.merge(df_lines, df_groupassigns, on=['ElemID','Level'])

#merge the line data with AISC weight information for that section
#note: if section is not in AISC table, weight (W) is assigned as zero (0) NOTE: weight in AISC table is in lbs/ft

df_lines = pd.merge(df_lines, df_AISC[['AISC_Manual_Label','W']], left_on = 'Section', right_on = 'AISC_Manual_Label', how='left', indicator=True)
df_lines = df_lines.replace(np.nan, 0)

#save df to text file for review
df_lines.to_csv('merged_output.txt', sep='\t', index=False)

#preview dataframe
df_lines


ElemID Level               Section ElemType iPointID jPointID  \
0        C1   L01  BU-WF-26X26X6X6-GR50   COLUMN        1        1   
1        C1   L02  BU-WF-26X26X6X6-GR50   COLUMN        1        1   
2        C1   L03               W14X665   COLUMN        1        1   
3        C1   L04               W14X665   COLUMN        1        1   
4        C1   L05               W14X455   COLUMN        1        1   
...     ...   ...                   ...      ...      ...      ...   
3366   L359   L05                  NONE     LINE       29       18   
3367   L359   L06                  NONE     LINE       29       18   
3368   L359   L07                  NONE     LINE       29       18   
3369   L359   L08                  NONE     LINE       29       18   
3370   L359   L09                  NONE     LINE       29       18   

      MultiLevel          Group AISC_Manual_Label      W     _merge  
0              1  BRB-X-Col.-T1                 0    0.0  left_only  
1              1  BRB-X-Col.-T1                 0    0.0  left_only  
2              1  BRB-X-Col.-T2           W14X665  665.0       both  
3              1  BRB-X-Col.-T2           W14X665  665.0       both  
4              1  BRB-X-Col.-T3           W14X455  455.0       both  
...          ...            ...               ...    ...        ...  
3366           0           CLAD                 0    0.0  left_only  
3367           0           CLAD                 0    0.0  left_only  
3368           0           CLAD                 0    0.0  left_only  
3369           0           CLAD                 0    0.0  left_only  
3370           0           CLAD                 0    0.0  left_only  

[3371 rows x 11 columns]

In [ ]:
#~~~needs to be rewritten to delete duplicate data in order to run multiple times

#merge df_lines key:iPointID with df_pointcoordinates key:PointID to find x,y of that point (rename column: ix, iy) and set iz = 0
#merge df_lines key:jPointID with df_pointcoordinates key:PointID to find x,y of that point (rename column: jx, jy)
#if Multilevel > 0, assign jz as the pd.merge values in df_stories key:Level
#calculate vector distance between (ix,iy, iz) and (jx, jy, jz)

###import ix, iy, set iz to zero
df_lines = pd.merge(df_lines, df_pointcoordinates, left_on = 'iPointID', right_on = 'PointID')
df_lines = df_lines.rename(columns={'x': 'ix', 'y': 'iy'})
df_lines['iz'] = 0

###import jx, jy, import jz
df_lines = pd.merge(df_lines, df_pointcoordinates, left_on = 'jPointID', right_on = 'PointID')
df_lines = pd.merge(df_lines, df_stories[['Level','Height']], on='Level')
df_lines = df_lines.rename(columns={'x': 'jx', 'y': 'jy', 'Height':'jz'})
df_lines[['MultiLevel','ix', 'iy', 'iz', 'jx', 'jy', 'jz']] = df_lines[['MultiLevel','ix', 'iy', 'iz', 'jx', 'jy', 'jz']].astype(float)

df_lines.loc[df_lines['MultiLevel'] == 0, 'jz'] = 0

###define function to calculate vector distance of element
def calculate_distance(row):
    x1, y1, z1 = row['ix'], row['iy'], row['iz']
    x2, y2, z2 = row['jx'], row['jy'], row['jz']
    distance = np.sqrt((x2 - x1)**2 + (y2 - y1)**2 + (z2 - z1)**2)
    return distance

#Apply function to each row
df_lines['Length'] = df_lines.apply(calculate_distance, axis=1)

#if e2k file length units are inches, divide W by 12 to get unit weight in inches.
#compute weight of element, given AISC default 'W' weight units are lb/ft

length_conversion = 1
if fileunit_length == 'in':
  length_conversion = 1/12

df_lines['W'] = df_lines['W']*length_conversion

weight_conversion = 1
if fileunit_weight == 'kip':
  weight_conversion = 1/1000

df_lines['W'] = df_lines['W']*weight_conversion

df_lines


ElemID Level                  Section ElemType iPointID jPointID  \
0        C1   L01     BU-WF-26X26X6X6-GR50   COLUMN        1        1   
1        B1   L01                  W21X275     BEAM        1        3   
2        C3   L01     BU-WF-26X26X6X6-GR50   COLUMN        3        3   
3      L349   L01                     NONE     LINE       19        3   
4        D2   L01  CoreBRB_28.00_BoltedLug    BRACE        1       19   
...     ...   ...                      ...      ...      ...      ...   
3366   B139   L10                   W21X48     BEAM      145      146   
3367   B140   L10                   W21X48     BEAM      149      150   
3368   B141   L10                   W21X48     BEAM      153      154   
3369   B142   L10                   W21X48     BEAM      157      158   
3370   B143   L10                   W21X48     BEAM      161      162   

      MultiLevel          Group AISC_Manual_Label         W     _merge  \
0            1.0  BRB-X-Col.-T1                 0  0.000000  left_only   
1            0.0   BRB-X-Bm.-T1           W21X275  0.022917       both   
2            1.0  BRB-X-Col.-T1                 0  0.000000  left_only   
3            0.0           CLAD                 0  0.000000  left_only   
4            1.0   BRB-X-Br.-T1                 0  0.000000  left_only   
...          ...            ...               ...       ...        ...   
3366         0.0         G-BM 2            W21X48  0.004000       both   
3367         0.0         G-BM 2            W21X48  0.004000       both   
3368         0.0         G-BM 2            W21X48  0.004000       both   
3369         0.0         G-BM 2            W21X48  0.004000       both   
3370         0.0         G-BM 2            W21X48  0.004000       both   

     PointID_x        ix        iy   iz PointID_y        jx        jy     jz  \
0            1 -2878.141 -5149.223  0.0         1 -2878.141 -5149.223  204.0   
1            1 -2878.141 -5149.223  0.0         3 -2500.141 -5149.223    0.0   
2            3 -2500.141 -5149.223  0.0         3 -2500.141 -5149.223  204.0   
3           19 -2689.141 -5149.223  0.0         3 -2500.141 -5149.223    0.0   
4            1 -2878.141 -5149.223  0.0        19 -2689.141 -5149.223  204.0   
...        ...       ...       ...  ...       ...       ...       ...    ...   
3366       145 -2500.141 -2251.223  0.0       146 -2044.141 -2251.223    0.0   
3367       149 -2500.141 -1999.223  0.0       150 -2044.141 -1999.223    0.0   
3368       153 -2500.141 -1873.223  0.0       154 -2044.141 -1873.223    0.0   
3369       157 -2500.141 -1621.223  0.0       158 -2044.141 -1621.223    0.0   
3370       161 -2500.141 -1495.223  0.0       162 -2044.141 -1495.223    0.0   

          Length  
0     204.000000  
1     378.000000  
2     204.000000  
3     189.000000  
4     278.095307  
...          ...  
3366  456.000000  
3367  456.000000  
3368  456.000000  
3369  456.000000  
3370  456.000000  

[3371 rows x 20 columns]

# Assemble Area Quantity Table

In [ ]:
#merge the area assignments (comprised of a value entry for each line label in the model) with the area connectivity (describing how that line connects to joint labels)
#note: the labels are not unique IDs; each line label can represent multiple lines that are identical across multiple floors

df_areas = pd.merge(df_areaassigns,df_areaconnectivity, on='ElemID')

In [ ]:
###import ix, iy
df_areas = pd.merge(df_areas, df_pointcoordinates, left_on = 'iPointID', right_on = 'PointID')
df_areas = df_areas.rename(columns={'x': 'ix', 'y': 'iy'}).drop(['PointID'], axis=1)


In [ ]:

# ###import jx, jy
df_areas = pd.merge(df_areas, df_pointcoordinates, left_on = 'jPointID', right_on = 'PointID')
df_areas = df_areas.rename(columns={'x': 'jx', 'y': 'jy'}).drop(['PointID'], axis=1)

In [ ]:
# ###import kx, ky
df_areas = pd.merge(df_areas, df_pointcoordinates, left_on = 'kPointID', right_on = 'PointID')
df_areas = df_areas.rename(columns={'x': 'kx', 'y': 'ky'}).drop(['PointID'], axis=1)

In [ ]:
# ###import lx, ly
df_areas = pd.merge(df_areas, df_pointcoordinates, left_on = 'lPointID', right_on = 'PointID')
df_areas = df_areas.rename(columns={'x': 'lx', 'y': 'ly'}).drop(['PointID'], axis=1)


additional area calculations

In [ ]:
#Calculate area of each area element based on i,j,k,l corner points and add 'Area' Column with computed area in default export units
df_areas[['ix', 'iy', 'jx', 'jy', 'kx', 'ky', 'lx', 'ly']] = df_areas[['ix', 'iy', 'jx', 'jy', 'kx', 'ky', 'lx', 'ly']].astype(float)
df_areas['Area'] =  0.5 * abs(df_areas['ix']*df_areas['jy'] + df_areas['jx']*df_areas['ky'] + df_areas['kx']*df_areas['ly'] + df_areas['lx']*df_areas['iy'] - (df_areas['iy']*df_areas['jx'] + df_areas['jy']*df_areas['kx'] + df_areas['ky']*df_areas['lx'] + df_areas['ly']*df_areas['ix']))

Define Deck Assignments

In [ ]:
df = get_table('$ DECK PROPERTIES',filepath)
df = df[[1, 11, 13, 23]]
df = df.rename(columns={1: 'Section', 11: 'SlabDepth', 13: 'RibDepth', 23: 'DeckUnitWeight'})
df[['SlabDepth', 'RibDepth', 'DeckUnitWeight']] = df[['SlabDepth', 'RibDepth', 'DeckUnitWeight']].astype(float)
df_decksections = df

In [ ]:
df_areas

ElemID Level           Section ElemType iPointID jPointID kPointID  \
0       F1   L01  SD3+4.5-4KSI-NWC    FLOOR       73       59        9   
1       F1   L02  SD3+4.5-4KSI-NWC    FLOOR       73       59        9   
2       F1   L03  SD3+4.5-4KSI-NWC    FLOOR       73       59        9   
3       F1   L04  SD3+4.5-4KSI-NWC    FLOOR       73       59        9   
4       F1   L05  SD3+4.5-4KSI-NWC    FLOOR       73       59        9   
..     ...   ...               ...      ...      ...      ...      ...   
388    F38   L05  SD3+4.5-4KSI-NWC    FLOOR       81       62       15   
389    F38   L06  SD3+4.5-4KSI-NWC    FLOOR       81       62       15   
390    F38   L07  SD3+4.5-4KSI-NWC    FLOOR       81       62       15   
391    F38   L08  SD3+4.5-4KSI-NWC    FLOOR       81       62       15   
392    F38   L09  SD3+4.5-4KSI-NWC    FLOOR       81       62       15   

    lPointID        ix        iy        jx        jy        kx        ky  \
0          2 -2878.141 -235.2232 -2500.141 -235.2232 -2500.141  142.7768   
1          2 -2878.141 -235.2232 -2500.141 -235.2232 -2500.141  142.7768   
2          2 -2878.141 -235.2232 -2500.141 -235.2232 -2500.141  142.7768   
3          2 -2878.141 -235.2232 -2500.141 -235.2232 -2500.141  142.7768   
4          2 -2878.141 -235.2232 -2500.141 -235.2232 -2500.141  142.7768   
..       ...       ...       ...       ...       ...       ...       ...   
388       82 -1666.141 -991.2232 -2044.141 -991.2232 -2044.141 -613.2232   
389       82 -1666.141 -991.2232 -2044.141 -991.2232 -2044.141 -613.2232   
390       82 -1666.141 -991.2232 -2044.141 -991.2232 -2044.141 -613.2232   
391       82 -1666.141 -991.2232 -2044.141 -991.2232 -2044.141 -613.2232   
392       82 -1666.141 -991.2232 -2044.141 -991.2232 -2044.141 -613.2232   

           lx        ly      Area  
0   -2878.141  142.7768  142884.0  
1   -2878.141  142.7768  142884.0  
2   -2878.141  142.7768  142884.0  
3   -2878.141  142.7768  142884.0  
4   -2878.141  142.7768  142884.0  
..        ...       ...       ...  
388 -1666.141 -613.2232  142884.0  
389 -1666.141 -613.2232  142884.0  
390 -1666.141 -613.2232  142884.0  
391 -1666.141 -613.2232  142884.0  
392 -1666.141 -613.2232  142884.0  

[393 rows x 17 columns]

# Calculate Total Project Areas (Roper-Specific)



In [ ]:
#get total project area in order to calculate PSF values

pv_PSF = pd.pivot_table(df_areas, values=(['Area']), index='Level', aggfunc='sum', margins = 'True', margins_name='Grand Total')
pv_PSF['Area (ft^2)'] = pv_PSF['Area']/144

# for Framed Area Values
slab_on_deck_column= pv_PSF.columns.get_loc("Area (ft^2)"); slab_on_deck_row= -1
slab_on_deck_ft = (int(math.ceil(pv_PSF.iat[slab_on_deck_row,slab_on_deck_column])))

suspended_slab_column= pv_PSF.columns.get_loc("Area (ft^2)"); suspended_slab_row= pv_PSF.index.get_loc("L01");
suspended_slab_ft= (int(math.ceil(pv_PSF.iat[suspended_slab_row,suspended_slab_column])))

total_area_ft = slab_on_deck_ft + suspended_slab_ft

In [ ]:
print("total slab on deck (ft) =", slab_on_deck_ft)
print("total suspended slab (ft) =", suspended_slab_ft)
print("total framed area (ft) =", total_area_ft)


total slab on deck (ft) = 416777
total suspended slab (ft) = 44541
total framed area (ft) = 461318


# Calculate Frame Quantity Summaries (Roper-Specific)

## Generate Pivot Tables
>**pv_linesummary**: summary weights for system categories <br> **pv_brace**: summary info of BRB brace elements


pv_linesummary

In [ ]:
#add total weight of member by multiplying unit weight (W) by length (Length)
df_lines['Weight'] = df_lines['W']*df_lines['Length'] #weight (kip/in)*(in)
#add column for category of group, ie. BRB.. = B, Gravity = G, Moment Frame = M
df_lines['Category'] = df_lines['Group'].str[0]

In [ ]:
df_lines

ElemID Level                  Section ElemType iPointID jPointID  \
0        C1   L01     BU-WF-26X26X6X6-GR50   COLUMN        1        1   
1        B1   L01                  W21X275     BEAM        1        3   
2        C3   L01     BU-WF-26X26X6X6-GR50   COLUMN        3        3   
3      L349   L01                     NONE     LINE       19        3   
4        D2   L01  CoreBRB_28.00_BoltedLug    BRACE        1       19   
...     ...   ...                      ...      ...      ...      ...   
3366   B139   L10                   W21X48     BEAM      145      146   
3367   B140   L10                   W21X48     BEAM      149      150   
3368   B141   L10                   W21X48     BEAM      153      154   
3369   B142   L10                   W21X48     BEAM      157      158   
3370   B143   L10                   W21X48     BEAM      161      162   

      MultiLevel          Group AISC_Manual_Label         W  ...        ix  \
0            1.0  BRB-X-Col.-T1                 0  0.000000  ... -2878.141   
1            0.0   BRB-X-Bm.-T1           W21X275  0.022917  ... -2878.141   
2            1.0  BRB-X-Col.-T1                 0  0.000000  ... -2500.141   
3            0.0           CLAD                 0  0.000000  ... -2689.141   
4            1.0   BRB-X-Br.-T1                 0  0.000000  ... -2878.141   
...          ...            ...               ...       ...  ...       ...   
3366         0.0         G-BM 2            W21X48  0.004000  ... -2500.141   
3367         0.0         G-BM 2            W21X48  0.004000  ... -2500.141   
3368         0.0         G-BM 2            W21X48  0.004000  ... -2500.141   
3369         0.0         G-BM 2            W21X48  0.004000  ... -2500.141   
3370         0.0         G-BM 2            W21X48  0.004000  ... -2500.141   

            iy   iz  PointID_y        jx        jy     jz      Length  Weight  \
0    -5149.223  0.0          1 -2878.141 -5149.223  204.0  204.000000  0.0000   
1    -5149.223  0.0          3 -2500.141 -5149.223    0.0  378.000000  8.6625   
2    -5149.223  0.0          3 -2500.141 -5149.223  204.0  204.000000  0.0000   
3    -5149.223  0.0          3 -2500.141 -5149.223    0.0  189.000000  0.0000   
4    -5149.223  0.0         19 -2689.141 -5149.223  204.0  278.095307  0.0000   
...        ...  ...        ...       ...       ...    ...         ...     ...   
3366 -2251.223  0.0        146 -2044.141 -2251.223    0.0  456.000000  1.8240   
3367 -1999.223  0.0        150 -2044.141 -1999.223    0.0  456.000000  1.8240   
3368 -1873.223  0.0        154 -2044.141 -1873.223    0.0  456.000000  1.8240   
3369 -1621.223  0.0        158 -2044.141 -1621.223    0.0  456.000000  1.8240   
3370 -1495.223  0.0        162 -2044.141 -1495.223    0.0  456.000000  1.8240   

      Category  
0            B  
1            B  
2            B  
3            C  
4            B  
...        ...  
3366         G  
3367         G  
3368         G  
3369         G  
3370         G  

[3371 rows x 22 columns]

In [ ]:
#summary system weights (kip)
pv_linesummary = pd.pivot_table(df_lines, values='Weight', columns='ElemType', index='Category', aggfunc='sum', margins = 'True', margins_name='Grand Total')
pv_linesummary = pv_linesummary.drop([('LINE'), ('BRACE')], axis=1).drop(('C'),axis=0).round(0)

In [ ]:
kip_to_tons = 0.5
kip_to_pounds = 1000

pv_linesummary['Beam (tons)'] = pv_linesummary['BEAM']*kip_to_tons
pv_linesummary['Column (tons)'] = pv_linesummary['COLUMN']*kip_to_tons
pv_linesummary['Total (tons)'] = pv_linesummary['Grand Total']*kip_to_tons

pv_linesummary['Beam (PSF)'] = pv_linesummary['BEAM']*kip_to_pounds/slab_on_deck_ft
pv_linesummary['Column (PSF)'] = pv_linesummary['COLUMN']*kip_to_pounds/slab_on_deck_ft
pv_linesummary['Total (PSF)'] = pv_linesummary['Grand Total']*kip_to_pounds/slab_on_deck_ft

pv_linesummary = pv_linesummary.drop(columns=['BEAM','COLUMN','Grand Total']).round(1)

pv_brace

In [ ]:
pivot1 = df_lines[df_lines['Category'] == 'B']
pivot1 = pivot1[pivot1['Group'].str.contains('Br.')]
#identify all the brb sizes by extracting portion of string that is a float
pivot1['BRBSize'] = pivot1['Section'].str.extract(r'(\d+)').astype(float)
pivot1['BRBDirection'] = pivot1['Group'].str[4]

#calculate BRB steel weight
steel_density = 0.284/1000 #kip/in^3
pivot1['BRBWeight'] = pivot1['BRBSize']*pivot1['Length']*steel_density

#create initial pivot table
pv_brace = pd.pivot_table(pivot1, values='BRBSize', columns='BRBDirection', index='Level', aggfunc='mean', margins = 'True', margins_name='Grand Total')

# # ~~~~this next line may not work once there is x and y - need to troubleshoot!
pv_brace = pv_brace.join(pd.pivot_table(pivot1, values = "Category", columns = "BRBDirection", index = 'Level', aggfunc ='count', margins = 'True', margins_name='Grand Total'),how='right', rsuffix='count')

#add weight from BRBs
pv_brace['Weight'] = pd.pivot_table(pivot1, values='BRBWeight', index='Level', aggfunc='sum',margins = 'True', margins_name='Grand Total').round(0)


In [ ]:
# Additional Formatting

# Function to rename a column conditionally
def rename_column_if_exists(df, old_name, new_name):
    if old_name in df.columns:
        df = df.rename(columns={old_name: new_name})
    return df

# Function to delete last entry of column
def delete_last_entry(df, col_name):
    if col_name in df.columns:
          df.at[df.index[-1], col_name] = ""
    return df

columns_to_remove = [col for col in pv_brace.columns if col.startswith('Grand')]
pv_brace = pv_brace.drop(columns=columns_to_remove)

kip_to_tons = 0.5
pv_brace['Weight'] = pv_brace['Weight']*kip_to_tons
pv_brace = pv_brace.rename(columns={'Weight': 'Weight (tons)'})

# Rename the column if it exists and remove the averaged Grand Total values
pv_brace = rename_column_if_exists(pv_brace, 'X', 'X-Brace (in^2)')
pv_brace = delete_last_entry(pv_brace, 'X-Brace (in^2)')
pv_brace = rename_column_if_exists(pv_brace, 'Y', 'Y-Brace (in^2)')
pv_brace = delete_last_entry(pv_brace, 'Y-Brace (in^2)')

<ipython-input-59-45bc2e59f257>:12: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  df.at[df.index[-1], col_name] = ""


## Frame Summary Results

In [ ]:
print("Summary weights (kip) per system *excluding BRB Core Sections*")
display(pv_linesummary)

print("BRB summary including count and weight (kip) per bracing direction")
display(pv_brace)

Summary weights (kip) per system *excluding BRB Core Sections*


ElemType     Beam (tons)  Column (tons)  Total (tons)  Beam (PSF)  \
Category                                                            
B                  810.5          748.0        1558.5         3.9   
G                 1347.5          395.0        1742.5         6.5   
Grand Total       2158.0         1143.0        3301.0        10.4   

ElemType     Column (PSF)  Total (PSF)  
Category                                
B                     3.6          7.5  
G                     1.9          8.4  
Grand Total           5.5         15.8

BRB summary including count and weight (kip) per bracing direction


BRBDirection X-Brace (in^2) Y-Brace (in^2)  Xcount  Ycount  Weight (tons)
Level                                                                    
L01                    28.0           28.0      22      24           52.5
L02                    28.0           28.0      22      24           55.5
L03                    24.0           26.0      22      24           43.5
L04                    24.0           26.0      22      24           43.5
L05                    22.0           24.0      22      24           40.0
L06                    22.0           24.0      22      24           40.0
L07                    22.0           24.0      22      24           40.0
L08                    22.0           24.0      22      24           40.0
L09                    22.0           24.0      22      24           40.0
L10                    22.0           24.0       4      24           29.0
Grand Total                                    202     240          424.0

#Calculate Area Quantities (Roper-Specific)

## Generate Pivot Tables

In [ ]:
#calculate area element weight based on deck section assignment
df_areas = pd.merge(df_areas, df_decksections, on='Section')
concrete_density = 150/1000/(12*12*12) #150 lb/ft^3 converted to kip/in^3
# df_areas['Weight'] = df_areas['Area']*df_areas['UnitWeight']
df_areas['ConcreteWeight'] = df_areas['Area']*(df_areas['SlabDepth']+df_areas['RibDepth']/2)*concrete_density #wrong
df_areas['DeckWeight'] = df_areas['Area']*df_areas['DeckUnitWeight']

In [ ]:
#summary system weights (kip)
pv_areasummary = pd.pivot_table(df_areas, values=(['Area','ConcreteWeight', 'DeckWeight']), index='Level', aggfunc='sum', margins = 'True', margins_name='Grand Total')
pv_areasummary['Area (ft^2)'] = pv_areasummary['Area']/144

pv_areasummary['Volume'] = pv_areasummary['ConcreteWeight']/concrete_density
pv_areasummary['Volume (ft^3)'] = pv_areasummary['Volume']/(12*12*12)

pv_areasummary = pv_areasummary.round(1)


In [ ]:
pv_areasummary

Area  ConcreteWeight  DeckWeight  Area (ft^2)       Volume  \
Level                                                                           
L01           6413903.8          3340.6       120.3      44541.0   38483422.5   
L02           6413903.8          3340.6       120.3      44541.0   38483422.5   
L03           6413903.8          3340.6       120.3      44541.0   38483422.5   
L04           6413903.8          3340.6       120.3      44541.0   38483422.5   
L05           6413903.8          3340.6       120.3      44541.0   38483422.5   
L06           6413903.8          3340.6       120.3      44541.0   38483422.5   
L07           6413903.8          3340.6       120.3      44541.0   38483422.5   
L08           6413903.8          3340.6       120.3      44541.0   38483422.5   
L09           6413903.8          3340.6       120.3      44541.0   38483422.5   
L10           2290680.0          1889.0        43.0      15907.5   21761460.0   
Grand Total  60015813.8         31954.2      1125.3     416776.5  368112262.9   

             Volume (ft^3)  
Level                       
L01                22270.5  
L02                22270.5  
L03                22270.5  
L04                22270.5  
L05                22270.5  
L06                22270.5  
L07                22270.5  
L08                22270.5  
L09                22270.5  
L10                12593.4  
Grand Total       213027.9

In [ ]:
# Additional Formatting

#filter for relevant catagories
pv_areasummary2 = pv_areasummary.loc[:, ['Area (ft^2)', 'Volume (ft^3)','DeckWeight']]

#steel deck data
pv_areasummary2["Steel Deck Weight (tons)"] = pv_areasummary2["DeckWeight"]/2
pv_areasummary2 = pv_areasummary2.drop(columns=["DeckWeight"])

#concrete data
pv_areasummary2["Conc. Volume (CuY)"] = pv_areasummary2["Volume (ft^3)"]/27
pv_areasummary2 = pv_areasummary2.drop(columns=["Volume (ft^3)"])

# Keep only the first and last rows of the DataFrame, suspended slab is taken as equivalent as L01 with overridden concrete vol.
if len(pv_areasummary2) > 2:
    pv_areasummary2 = pd.concat([pv_areasummary2.iloc[[0]], pv_areasummary2.iloc[[-1]]])
elif len(pv_areasummary2) == 2:
    pv_areasummary2 = pv_areasummary2
elif len(pv_areasummary2) == 1:
    pv_areasummary2 = pv_areasummary2
else:
    print("DataFrame is empty")

pv_areasummary2 = pv_areasummary2.rename(index={"L01":"Suspended Slab", "Grand Total":"Slab on Deck"})

# Function to delete last entry of column
def delete_first_entry(df, col_name):
    if col_name in df.columns:
          df.at[df.index[0], col_name] = ""
    return df

# manually adjust the suspended slab data ... remove illogical steel deck weight in suspended slab (remaining from when we took L01 as suspended slab)
# pv_areasummary2 = delete_first_entry(pv_areasummary2, 'Steel Deck Weight (kip)')
pv_areasummary2.loc['Suspended Slab', 'Conc. Volume (CuY)'] = pv_areasummary2.loc['Suspended Slab', 'Area (ft^2)']/27 # to represent 1ft*area(ft) = 12" thick suspended slab
pv_areasummary2.loc['Suspended Slab', 'Steel Deck Weight (tons)'] = ""
# adjust rounding
pv_areasummary2 = pv_areasummary2.round(1)

<ipython-input-64-902403dea26f>:35: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  pv_areasummary2.loc['Suspended Slab', 'Steel Deck Weight (tons)'] = ""


In [ ]:
# sqft = ([suspended_slab_ft,slab_on_deck_ft])
# sqft = pd.DataFrame(sqft)
# pv_areasummary2.join(sqft)

## Area Summary Results

In [ ]:
print("Deck Area per floor (in^2) and Weights per Floor (kip)")
display(pv_areasummary2)

Deck Area per floor (in^2) and Weights per Floor (kip)


Area (ft^2) Steel Deck Weight (tons)  Conc. Volume (CuY)
Level                                                                   
Suspended Slab      44541.0                                       1649.7
Slab on Deck       416776.5                   562.65              7889.9

# Format as HTML

In [ ]:
# Function to format numbers with commas
def format_with_commas(x):
    if isinstance(x, (int, float)):
        return f"{x:,}"
    return x

info_brace = pv_brace.style.format(format_with_commas)
info_brace = info_brace.to_html(index=True)

info_frame = pv_linesummary.style.format(format_with_commas)
info_frame = info_frame.to_html(index=True)

info_area = pv_areasummary2.style.format(format_with_commas)
info_area = info_area.to_html(index=True)

# info_brace = pv_brace.to_html(index=True)
# info_frame = pv_linesummary.to_html(index=True)
# info_area = pv_areasummary.to_html(index=True)

# for Framed Area Results
slab_on_deck = "{:,}".format(int(slab_on_deck_ft))
suspended_slab = "{:,}".format(int(suspended_slab_ft))
total_area = "{:,}".format(int(total_area_ft))


In [ ]:
combined_html = f"""

<html>
<head>
    <title>DataFrame Tables</title>
</head>
<body>

    <h1><b>{filepath}</b></h1>

    <h2><b>Framed Area</b></h2>
    <p style='display: inline;'>Slab on Deck: {slab_on_deck} ft<sup>2<sup><p>
    <p style='display: inline;'>Suspended Slab: {suspended_slab} ft<sup>2<sup><p>
    <p style='display: inline;'>Total Framed Area: {total_area} ft<sup>2<sup><p>

    <h1>Frame Info</h1>
    {info_frame}
    <h1>Brace Info</h1>
    {info_brace}
    <h1>Area Info</h1>
    {info_area}


</body>
</html>
"""

# Final Report

In [ ]:
# Step 4: Write the combined HTML to a file
with open('/content/dataframes.html', 'w') as f:
    f.write(combined_html)

# Step 5: Display the HTML file in Colab
display(HTML(combined_html))

# Send To Excel


In [ ]:
# with pd.ExcelWriter('Template_Quantities.xlsx') as writer:
#   pv_areasummary.to_excel(writer, sheet_name='area_pivot_table', index=False)
#   pv_linesummary.to_excel(writer, sheet_name='frame_pivot_table', index=False)
#   pv_brace.to_excel(writer, sheet_name='brb_pivot_table', index=False)

In [ ]:
# with pd.ExcelWriter(
#     'Template_Quantities.xlsx',
#     mode="a",
#     engine="openpyxl",
#     if_sheet_exists="overlay",
# ) as writer:
#     pv_areasummary.to_excel(writer, sheet_name='area_pivot_table', index=True)
#     pv_linesummary.to_excel(writer, sheet_name='frame_pivot_table', index=True)
#     pv_brace.to_excel(writer, sheet_name='brb_pivot_table', index=True)

# Import Column Joint Reactions

In [ ]:
file_path = "testbasereactions.xlsx"

#######evaluate units more carefully for the excel sheet - or make sure they are exported to access using the right units!
# Read the first two rows to get headers and sub-headers
headers = pd.read_excel(file_path, header=[1])

# Read the actual data, skipping the first two rows used for headers
df_jointreactions = pd.read_excel(file_path, skiprows=[0, 1,2])

# Set the MultiIndex columns
df_jointreactions.columns = headers.columns

df_jointreactions

Story  Label  Unique Name         Output Case    Case Type Step Type  \
0      L00      1            1       RSX-STR (ELF)  Combination       Min   
1      L00      1            1       RSY-STR (ELF)  Combination       Max   
2      L00      1            1       RSY-STR (ELF)  Combination       Min   
3      L00      1            1  RS100X30Y_EP (ELF)  Combination       Max   
4      L00      1            1  RS100X30Y_EP (ELF)  Combination       Min   
...    ...    ...          ...                 ...          ...       ...   
1314   L00     83          728              ENV_UF  Combination       Min   
1315   L00     83          728   RSX-STR_dYP (ELF)  Combination       Max   
1316   L00     83          728   RSX-STR_dYP (ELF)  Combination       Min   
1317   L00     83          728   RSY-STR_dXP (ELF)  Combination       Max   
1318   L00     83          728   RSY-STR_dXP (ELF)  Combination       Min   

           FX     FY        FZ  MX  MY  MZ  
0    -347.683 -0.606 -2445.331   0   0   0  
1       0.178  2.981     0.101   0   0   0  
2      -0.178 -2.981    -0.101   0   0   0  
3     406.814  1.620  2854.794   0   0   0  
4    -406.814 -1.620 -2854.794   0   0   0  
...       ...    ...       ...  ..  ..  ..  
1314   -1.107 -0.744   418.488   0   0   0  
1315    1.252  0.206     0.022   0   0   0  
1316   -1.252 -0.206    -0.022   0   0   0  
1317    0.037  1.356     0.001   0   0   0  
1318   -0.037 -1.356    -0.001   0   0   0  

[1319 rows x 12 columns]

In [ ]:
pv_jointsummarymax = pd.pivot_table(df_jointreactions, values=['FZ'], columns=['Label'], index = ['Output Case'], aggfunc=['max'])  #, margins = 'True', margins_name='Grand Total'
pv_jointsummarymin = pd.pivot_table(df_jointreactions, values=['FZ'], columns=['Label'], index = ['Output Case'], aggfunc=['min'])  #, margins = 'True', margins_name='Grand Total'



In [ ]:
pv_jointsummarymin

min                                             \
                          FZ                                              
Label                     1         2         3            4         5    
Output Case                                                               
ENV_UF              -234.898  -234.898   507.646   287.323000   233.666   
ENV_U_E            -2423.801 -2423.801   372.303 -1296.155000 -1373.042   
ENV_U_G             1008.699  1008.699  1284.543  2079.265000  2076.855   
ENV_U_W              500.053   498.093   757.666  1145.933000  1130.063   
RS100X30Y_EP (ELF) -2854.794 -2854.794  -179.695 -2198.310000 -2274.161   
RS30X100Y_EP (ELF)  -863.676  -863.676   -53.881  -643.081000  -645.976   
RSX-STR (ELF)      -2445.331 -2445.331  -156.215 -1988.794000 -2150.369   
RSX-STR_dYP (ELF)  -2823.935 -2823.935  -177.928 -2182.520000 -2264.823   
RSY-STR (ELF)         -0.101    -0.101    -0.100    -0.000157    -0.028   
RSY-STR_dXP (ELF)    -93.512   -93.513    -5.355   -47.848000   -28.297   
S1:D                 720.499   720.499   917.531  1485.189000  1483.468   
S2:D+L               975.553   975.553  1254.009  2299.559000  2296.870   

                                                                            \
                                                                             
Label                        6         7            8         9         10   
Output Case                                                                  
ENV_UF               297.320000   233.666   287.323000   507.646   507.646   
ENV_U_E             -805.927000 -1373.042 -1296.155000   372.303   372.303   
ENV_U_G             2204.885000  2076.855  2079.265000  1284.543  1284.543   
ENV_U_W             1204.642000  1130.541  1145.863000   754.453   755.335   
RS100X30Y_EP (ELF) -1770.510000 -2274.161 -2198.310000  -179.695  -179.695   
RS30X100Y_EP (ELF)  -482.866000  -645.976  -643.081000   -53.881   -53.881   
RSX-STR (ELF)      -1770.510000 -2150.369 -1988.794000  -156.215  -156.215   
RSX-STR_dYP (ELF)  -1770.510000 -2264.823 -2182.520000  -177.928  -177.928   
RSY-STR (ELF)         -0.000081    -0.028    -0.000181    -0.100    -0.100   
RSY-STR_dXP (ELF)     -0.000081   -28.297   -47.848000    -5.355    -5.355   
S1:D                1574.918000  1483.468  1485.189000   917.531   917.531   
S2:D+L              2369.571000  2296.870  2299.559000  1254.009  1254.009   

                    ...                                                  \
                    ...                                                   
Label               ...           74          75           76        77   
Output Case         ...                                                   
ENV_UF              ...   418.488000   418.69100   419.040000   418.664   
ENV_U_E             ...   418.467000   418.67600   419.028000   418.647   
ENV_U_G             ...  1008.649000  1009.19200  1009.998000  1009.128   
ENV_U_W             ...   584.196000   584.48700   584.968000   584.450   
RS100X30Y_EP (ELF)  ...    -0.023000    -0.01600    -0.012000    -0.017   
RS30X100Y_EP (ELF)  ...    -0.007000    -0.00500    -0.004000    -0.007   
RSX-STR (ELF)       ...    -0.020000    -0.01400    -0.011000    -0.016   
RSX-STR_dYP (ELF)   ...    -0.022000    -0.01500    -0.012000    -0.017   
RSY-STR (ELF)       ...    -0.000438    -0.00025    -0.000126    -0.002   
RSY-STR_dXP (ELF)   ...    -0.001000    -0.00100    -0.000297    -0.002   
S1:D                ...   720.463000   720.85100   721.427000   720.806   
S2:D+L              ...  1088.155000  1088.70000  1089.547000  1088.622   

                                                                           \
                                                                            
Label                     78        79        80           81          82   
Output Case                                                                 
ENV_UF               417.832   417.832   418.664   419.040000   41